In [1]:
import sys
print(sys.executable)
import os
print(os.getcwd())

/cluster/u/nikcaryo/software/miniconda/envs/amelie/bin/python
/cluster/u/nikcaryo/amelie-229/amelie


In [2]:
import argparse
import json
import multiprocessing
import os
import pickle
import random
import sys
from collections import defaultdict
import importlib
import constdb

import text_classification

dataloaders.hpo
<function parent_package_name at 0x7f18486445f0>
text_classification


In [3]:
def load_article(processed_dir, pmid):
    path = processed_dir + '/' + str(pmid) + '.pkl'

    if not os.path.isfile(path):
        return None
    else:
        with open(path, 'rb') as file:
            try:
                loaded = pickle.load(file)
                return loaded
            except EOFError:
                print("Cannot load pmid %s for some reason ..." % pmid, flush=True)
                return None

class ConvertToTextFunction:
    def __init__(self, processed_dir, replace_phenos_with_nothing):
        self.processed_dir = processed_dir
        self.replace_phenos_with_nothing = replace_phenos_with_nothing

    def __call__(self, pmid):
        processed_article = load_article(self.processed_dir, pmid)
        if processed_article is None:
            return None

        article = text_classification.convert_to_text(processed_article, use_main_text=True,
                                                      replace_phenos_with_nothing=self.replace_phenos_with_nothing)

        return pmid, article


def convert_all_to_text(processed_dir, pmids, replace_phenos_with_nothing):
    with multiprocessing.Pool(100) as pool:
        print('Pool created', flush=True)
        for i, item in enumerate(pool.imap_unordered(
                ConvertToTextFunction(processed_dir,
                                      replace_phenos_with_nothing=replace_phenos_with_nothing),
                pmids,
                chunksize=100)):
            if i % 10000 == 0:
                print('Processed ', i, ' out of ', len(pmids), flush=True)

            if item is not None:
                yield item

def shuffle_articles_labels(articles, labels):
    zipped_articles_labels = [x for x in zip(articles, labels)]
    random.shuffle(zipped_articles_labels)
    return [x for x in zip(*zipped_articles_labels)]

In [7]:
def train_text_field_classifier(out_dir, process_dir, field_name, save, cross_val, l1,
                                replace_phenos_with_nothing):
    with open(out_dir + '/dataset_meta.json') as file:
        dataset_info = json.load(file)

    with open(out_dir + '/omim.json') as file:
        omim = json.load(file)
    positives = set(dataset_info['positive_pmids'])
    print('Total positives: ', len(positives), flush=True)
    good_positives = []

    for pmid in positives:
        omim_data = omim[str(pmid)]
        print(omim_data)
        if field_name not in omim_data:
            continue
        field = omim_data[field_name]
        if len(field) == 0 or len(field) == 2:
            # Skip bad ones
            continue
        good_positives.append(pmid)
    
    print('Good positives: ', len(good_positives), flush=True)
    articles = []
    labels = []

    for pmid, article in convert_all_to_text(process_dir, good_positives,
                                             replace_phenos_with_nothing=replace_phenos_with_nothing):
        omim_data = omim[str(pmid)]
        field = omim_data[field_name]
        articles.append(article)
        labels.append(field[0])

    for pmid, article in convert_all_to_text(process_dir, dataset_info['gwas_pmids'],
                                             replace_phenos_with_nothing=replace_phenos_with_nothing):
        articles.append(article)
        labels.append('gwas')

    articles, labels = shuffle_articles_labels(articles, labels)
    
    # remove for actual training!
    articles = articles[:100]
    labels = labels[:100]

    print('Have ', len(articles), flush=True)
    counters = defaultdict(int)
    for label in labels:
        counters[label] += 1

    print('Counts per label:', counters, flush=True)
    print('Done converting', flush=True)
    classifier = text_classification.create_model(articles, labels, cross_val=cross_val, l1=l1)

    if save:
        print("SAVING TEXT FIELD RELEVANCE CLASSIFIER", flush=True)
        with open(out_dir + '/text_field_{}.pkl'.format(field_name), 'wb') as out_file:
            pickle.dump(classifier, out_file)
    else:
        print("NOT SAVING TEXT FIELD RELEVANCE CLASSIFIER", flush=True)

In [9]:
out_dir = "../../amelie-updated/amelie_out_dir"
process_dir = "../../amelie-updated/amelie_process_dir"

save = True
cross_val = True
l1=False
replace_phenos_with_nothing=False

# right now it's set to only use 100 papers
# training on all of the papers is p slow
train_text_field_classifier(out_dir, process_dir, "inheritance_modes", save, cross_val, l1,
                                replace_phenos_with_nothing)
# train_text_field_classifier(out_dir, process_dir, "variant_types", save, cross_val, l1,
#                                 replace_phenos_with_nothing)

Total positives:  59123
{'variant_types': [], 'inheritance_modes': [], 'topical_genes': ['ENSG00000171560', 'ENSG00000171557', 'ENSG00000171564']}
{'variant_types': [], 'inheritance_modes': [], 'topical_genes': ['ENSG00000156650']}
{'variant_types': [], 'inheritance_modes': [], 'topical_genes': ['ENSG00000087237']}
{'variant_types': [], 'inheritance_modes': [], 'topical_genes': ['ENSG00000070915']}
{'variant_types': [], 'inheritance_modes': [], 'topical_genes': ['ENSG00000118729', 'ENSG00000198626']}
{'variant_types': [], 'inheritance_modes': [], 'topical_genes': ['ENSG00000049768']}
{'variant_types': [], 'inheritance_modes': [], 'topical_genes': ['ENSG00000169297']}
{'variant_types': [], 'inheritance_modes': [], 'topical_genes': ['ENSG00000135100']}
{'variant_types': [], 'inheritance_modes': [], 'topical_genes': ['ENSG00000064270']}
{'variant_types': [], 'inheritance_modes': [], 'topical_genes': ['ENSG00000108439']}
{'variant_types': [], 'inheritance_modes': [], 'topical_genes': ['ENS

{'variant_types': [], 'inheritance_modes': [], 'topical_genes': ['ENSG00000166340', 'ENSG00000131238']}
{'variant_types': [], 'inheritance_modes': [], 'topical_genes': ['ENSG00000073282']}
{'variant_types': [], 'inheritance_modes': [], 'topical_genes': ['ENSG00000123560']}
{'variant_types': [], 'inheritance_modes': [], 'topical_genes': ['ENSG00000169554']}
{'variant_types': [], 'inheritance_modes': [], 'topical_genes': ['ENSG00000188419']}
{'variant_types': [], 'inheritance_modes': [], 'topical_genes': ['ENSG00000213639']}
{'variant_types': [], 'inheritance_modes': [], 'topical_genes': ['ENSG00000091137']}
{'variant_types': [], 'inheritance_modes': [], 'topical_genes': ['ENSG00000169562']}
{'variant_types': [], 'inheritance_modes': [], 'topical_genes': ['ENSG00000036473']}
{'variant_types': [], 'inheritance_modes': [], 'topical_genes': ['ENSG00000168263']}
{'variant_types': [], 'inheritance_modes': [], 'topical_genes': ['ENSG00000039068']}
{'variant_types': [], 'inheritance_modes': [],

{'variant_types': [], 'inheritance_modes': [], 'topical_genes': ['ENSG00000128591', 'ENSG00000140795']}
{'variant_types': [], 'inheritance_modes': [], 'topical_genes': ['ENSG00000163541']}
{'variant_types': [], 'inheritance_modes': [], 'topical_genes': ['ENSG00000007168']}
{'variant_types': [], 'inheritance_modes': [], 'topical_genes': ['ENSG00000204217']}
{'variant_types': [], 'inheritance_modes': [], 'topical_genes': ['ENSG00000131089']}
{'variant_types': [], 'inheritance_modes': [], 'topical_genes': ['ENSG00000244734']}
{'variant_types': [], 'inheritance_modes': [], 'topical_genes': ['ENSG00000164904']}
{'variant_types': [], 'inheritance_modes': [], 'topical_genes': ['ENSG00000124479', 'ENSG00000196767']}
{'variant_types': [], 'inheritance_modes': [], 'topical_genes': ['ENSG00000110711', 'ENSG00000133895', 'ENSG00000111276']}
{'variant_types': [], 'inheritance_modes': [], 'topical_genes': ['ENSG00000184895']}
{'variant_types': [], 'inheritance_modes': [], 'topical_genes': ['ENSG0000

{'variant_types': [], 'inheritance_modes': [], 'topical_genes': ['ENSG00000181523']}
{'variant_types': [], 'inheritance_modes': [], 'topical_genes': ['ENSG00000109501']}
{'variant_types': [], 'inheritance_modes': [], 'topical_genes': ['ENSG00000187714']}
{'variant_types': [], 'inheritance_modes': [], 'topical_genes': ['ENSG00000005471']}
{'variant_types': [], 'inheritance_modes': [], 'topical_genes': ['ENSG00000102978']}
{'variant_types': [], 'inheritance_modes': [], 'topical_genes': ['ENSG00000001626']}
{'variant_types': [], 'inheritance_modes': [], 'topical_genes': ['ENSG00000275410']}
{'variant_types': [], 'inheritance_modes': [], 'topical_genes': ['ENSG00000183873']}
{'variant_types': [], 'inheritance_modes': [], 'topical_genes': ['ENSG00000165091']}
{'variant_types': [], 'inheritance_modes': [], 'topical_genes': ['ENSG00000109501']}
{'variant_types': [], 'inheritance_modes': [], 'topical_genes': ['ENSG00000177628']}
{'variant_types': [], 'inheritance_modes': [], 'topical_genes': [

{'variant_types': [], 'inheritance_modes': [], 'topical_genes': ['ENSG00000277586']}
{'variant_types': [], 'inheritance_modes': [], 'topical_genes': ['ENSG00000160789']}
{'variant_types': [], 'inheritance_modes': [], 'topical_genes': ['ENSG00000244734']}
{'variant_types': [], 'inheritance_modes': [], 'topical_genes': ['ENSG00000188536']}
{'variant_types': [], 'inheritance_modes': [], 'topical_genes': ['ENSG00000180644']}
{'variant_types': [], 'inheritance_modes': [], 'topical_genes': ['ENSG00000244734']}
{'variant_types': [], 'inheritance_modes': [], 'topical_genes': ['ENSG00000188536']}
{'variant_types': [], 'inheritance_modes': [], 'topical_genes': ['ENSG00000188603']}
{'variant_types': [], 'inheritance_modes': [], 'topical_genes': ['ENSG00000244734']}
{'variant_types': [], 'inheritance_modes': [], 'topical_genes': ['ENSG00000118046', 'ENSG00000083093', 'ENSG00000108384', 'ENSG00000012048']}
{'variant_types': [], 'inheritance_modes': [], 'topical_genes': ['ENSG00000022267']}
{'varian

...

{'variant_types': [], 'inheritance_modes': [], 'topical_genes': ['ENSG00000169083']}
{'variant_types': [], 'inheritance_modes': [], 'topical_genes': ['ENSG00000136854', 'ENSG00000008086', 'ENSG00000136531', 'ENSG00000196876', 'ENSG00000107147', 'ENSG00000075043']}
{'variant_types': [], 'inheritance_modes': [], 'topical_genes': ['ENSG00000147889']}
{'variant_types': [], 'inheritance_modes': [], 'topical_genes': ['ENSG00000256269']}
{'variant_types': [], 'inheritance_modes': [], 'topical_genes': ['ENSG00000171298']}
{'variant_types': [], 'inheritance_modes': [], 'topical_genes': ['ENSG00000171298']}
{'variant_types': [], 'inheritance_modes': [], 'topical_genes': ['ENSG00000174697']}
{'variant_types': [], 'inheritance_modes': [], 'topical_genes': ['ENSG00000171298']}
{'variant_types': [], 'inheritance_modes': [], 'topical_genes': ['ENSG00000164692']}
{'variant_types': [], 'inheritance_modes': [], 'topical_genes': ['ENSG00000134982']}
{'variant_types': [], 'inheritance_modes': [], 'topical

{'variant_types': [], 'inheritance_modes': [], 'topical_genes': ['ENSG00000171759']}
{'variant_types': [], 'inheritance_modes': [], 'topical_genes': ['ENSG00000178802']}
{'variant_types': [], 'inheritance_modes': [], 'topical_genes': ['ENSG00000198400']}
{'variant_types': [], 'inheritance_modes': [], 'topical_genes': ['ENSG00000163541', 'ENSG00000136143']}
{'variant_types': [], 'inheritance_modes': [], 'topical_genes': ['ENSG00000104133']}
{'variant_types': [], 'inheritance_modes': [], 'topical_genes': ['ENSG00000184895']}
{'variant_types': [], 'inheritance_modes': [], 'topical_genes': ['ENSG00000144619']}
{'variant_types': [], 'inheritance_modes': [], 'topical_genes': ['ENSG00000132781']}
{'variant_types': [], 'inheritance_modes': [], 'topical_genes': ['ENSG00000106348']}
{'variant_types': [], 'inheritance_modes': [], 'topical_genes': []}
{'variant_types': [], 'inheritance_modes': [], 'topical_genes': ['ENSG00000188419']}
{'variant_types': [], 'inheritance_modes': [], 'topical_genes':

Pool created
Processed  0  out of  277
Pool created
Processed  0  out of  3345
Have  100
Counts per label: defaultdict(<class 'int'>, {'gwas': 92, 'dominant': 6, 'recessive': 2})
Done converting
Pipeline created
Five-fold cross validation
Scoring: micro


[Parallel(n_jobs=1)]: Using backend SequentialBackend with 1 concurrent workers.
/cluster/u/nikcaryo/software/miniconda/envs/amelie/lib/python3.7/site-packages/sklearn/model_selection/_split.py:626: Warning: The least populated class in y has only 2 members, which is too few. The minimum number of members in any class cannot be less than n_splits=5.
  % (min_groups, self.n_splits)), Warning)
/cluster/u/nikcaryo/software/miniconda/envs/amelie/lib/python3.7/site-packages/sklearn/linear_model/logistic.py:432: FutureWarning: Default solver will be changed to 'lbfgs' in 0.22. Specify a solver to silence this warning.
  FutureWarning)
/cluster/u/nikcaryo/software/miniconda/envs/amelie/lib/python3.7/site-packages/sklearn/linear_model/logistic.py:459: FutureWarning: Default multi_class will be changed to 'auto' in 0.22. Specify the multi_class option to silence this warning.
  "this warning.", FutureWarning)
[Parallel(n_jobs=1)]: Done   5 out of   5 | elapsed:    8.3s finished


Scores: 
{'fit_time': array([0.50825691, 0.5425024 , 0.55605602, 0.53204083, 0.53841138]), 'score_time': array([0.26828599, 0.20886779, 0.1964345 , 0.22481561, 0.21641684]), 'test_precision': array([0.86363636, 0.9047619 , 0.94736842, 0.94736842, 0.94736842]), 'train_precision': array([0.93589744, 0.92405063, 0.91358025, 0.91358025, 0.91358025]), 'test_recall': array([0.86363636, 0.9047619 , 0.94736842, 0.94736842, 0.94736842]), 'train_recall': array([0.93589744, 0.92405063, 0.91358025, 0.91358025, 0.91358025])}
Fitting classifier
SAVING TEXT FIELD RELEVANCE CLASSIFIER
